In [27]:
import pandas as pd
from difflib import get_close_matches

In [28]:
pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

# Intermediate Cleaning Step
Even after cleaning the transfermarkt player names for special characters in tableau the lef join operation, where the left df is the fbref dataset, we get 169 mismatched names in the fbref data.

Upon close inspectino in Tableau we realize the issue for many of this mismatches is that player names are often reported with shorter versions of their name in one data set vs the other, or with middle name vs no middle names in the other.

Due to the diversity of discrepancies in names, the best solution is to perform fuzzy matching. Tableau is reportedly poor at this task and thus we decided to perform this intermediate cleaning step in python before returning to Tableau to perform the final join between the fbref and transfermarkt data sets.

We use fuzzy matching to find and replace the fbref player name with its trasnfermarkt player name equivalent if possible. after we import the new fbref table with the more harmonized player names back into Tableau to peform the final merge.

### Loading Transfermarkt data cleaned in Tableau + fbref data cleaned in pycharm

In [160]:
transfermarkt_df = pd.read_csv('transfermarkt_player_marketvalue_cleaned.csv', index_col=0)

In [161]:
fbref_df = pd.read_csv('fbref_player_statistics.csv',index_col=0)

### Using fuzzy matching to replace player names in fbref data with transfermarkt variation if available

In [162]:
harmonized_names=[] #this is the list used to replace the player names in fbref
matched_pairs = dict() #to control quality of match we create matched_pairs dic + a no_match list
no_match = [] #if you wish to know how many are not found a match at all (for instance by varying cutoff parameter)
for i in fbref_df['Player']:
    close_match = get_close_matches(word=i, possibilities=transfermarkt_df['Player'], n=1, cutoff=.6)
    if close_match:
        matched_pairs[i] = close_match[0]
        harmonized_names.append(close_match[0])
    else:
        no_match.append(i)
        harmonized_names.append(i)

In [163]:
# fbref_df.sort_values('Player')

In [164]:
#controlling quality of match: we manually inspect dic of inexact matches to find wrong matches and generate a list to use
#as a filter that only adds th

sortedDict = dict(sorted(matched_pairs.items(), key=lambda x: x[0].lower()))
i=0
for k,v in sortedDict.items():
    if k!=v:
        print('{}:{}'.format(k,v))
        i+=1
print("# of inexact matches: " + str(i))


Abdul Majeed Waris:Majeed Waris
Adri Embarba:Adrian Embarba
Adrian Guerrero:Adria Guerrero
Alejandro Baena:Alessandro Berardi
Alejandro Blesa:Alessandro Berardi
Alejandro Pozo Pozo:Alejandro Pozo
Amad Traore:Adama Traore
Anderson Lima:Jefferson Lerma
Andre Frank Zambo Anguissa:Andre Zambo Anguissa
Angelo da Costa Junior:Angelo da Costa
Antonio Cortes:Antonio Puertas
Arthur Melo:Arthur
Baba Rahman:Benito Raman
Bryan:Bryan Gil
Cauly Oliveira Souza:Paulo Oliveira
Charalambos Lykogiannis:Charalampos Lykogiannis
Churripi:Chumi
Cristian Rivera:Christian Rivera
Dalbert Henrique:Caio Henrique
Dani Carvajal:Daniel Carvajal
Daniel Martin:Dani Martin
Daniel Parejo:Dani Parejo
Danilo Barbosa:Mariano Barbosa
Danilo Larangeira:Danilo Cataldi
Didier Ibrahim Ndong:Didier Ndong
Dimitris Siovas:Dimitrios Siovas
Eddy Salcedo:Eddie Salcedo
Edmilson Indjai:Edimilson Fernandes
Efthimis Koulouris:Efthymios Koulouris
Elie Youan:Thody Elie Youan
Elif Elmas:Eljif Elmas
Emerson Palmieri:Emerson
Emi Buendia:Emili

In [165]:
#through manual inspection of the inexact matches produced above, we determined a list of fbref that were found an 
#erroneous match in the transfermarkt names

wrong_matches = ['Alejandro Baena','Alejandro Blesa','Anderson Lima','Antonio Cortes','Baba Rahman','Cauly Oliveira Souza',
                 'Churripi','Dalbert Henrique','Danilo Larangeira','Edmilson Indjai', 'Espeto','Ezequiel Avila',
                 'Felipe dal Belo','Fernando Marcal','Fernando Nino', 'Fernando','Gabriel Dos Santos','Gleison Bremer',
                 'Jonny Castro','Jose Holebas','Kike','Lee Kangin','Louis Beyer','Mathias Jorgensen','Moanes Dabour',
                 'Nico Ribaudo','Obite NDicka','Opoku Ampomah','Raphael Dias Belloli','Raul','Thiago Alcantara'
                 'Thomas Doyle','Victor Perea','Vitorino Hilton','Yoel']

In [166]:
# replacing fbrefs old Player names column with the newly matched names
# fbref_df['Player'].replace(list(fbref_df['Player']), harmonized_names, inplace=True)

In [174]:
j = -1
for i in fbref_df['Player']:
    j+=1
    if i not in wrong_matches:
        fbref_df.loc[(fbref_df.Player==i),'Player'] = harmonized_names[j]
    else:
        continue

# fbref_df['Player_fuzzy'] = fbref_df['Player'].copy()
# j=-1
# for i in fbref_df['Player_fuzzy']:
#      j+=1
#      if i not in wrong_matches:
#          fbref_df['Player_fuzzy'][j]= harmonized_names[j]

In [177]:
fbref_df.sort_values('Player')

Player    Nation  Age                         Squad  \
501              Aaron Connolly       IRL   19                      Brighton   
538             Aaron Cresswell       ENG   29                      West Ham   
720             Aaron Escandell       ESP   23                       Granada   
1313               Aaron Lennon       ENG   32                       Burnley   
1325           Aaron Leya Iseka       BEL   21                      Toulouse   
1466               Aaron Martin       ESP   22                      Mainz 05   
1596                 Aaron Mooy       AUS   28                      Brighton   
1942             Aaron Ramsdale       ENG   21                   Bournemouth   
1943               Aaron Ramsey       WAL   28                      Juventus   
2466          Aaron Wan Bissaka       ENG   21                Manchester Utd   
1652             Abdallah Ndour       SEN   25                    Strasbourg   
1407          Abdallahi Mahmoud       MTN   19                        Alavés   
2052          Abdelhamid Sabiri       GER   22                  Paderborn 07   
1903                Abdon Prats       ESP   26                      Mallorca   
622                Abdou Diallo       FRA   23                     Paris S-G   
1150         Abdoul Kader Bamba       FRA   25                        Nantes   
171             Abdoulaye Bamba       CIV   29                        Angers   
665          Abdoulaye Doucoure       FRA   26                       Watford   
2350            Abdoulaye Toure       FRA   25                        Nantes   
1756              Abou Ouattara       BFA   19                         Lille   
973               Achraf Hakimi       MAR   20                      Dortmund   
290                 Adam Bodzek       GER   33                    Düsseldorf   
1061                  Adam Idah       IRL   18                  Norwich City   
1271               Adam Lallana       ENG   31                     Liverpool   
1481               Adam Marusic       MNE   26                         Lazio   
1483                Adam Masina       ITA   25                       Watford   
1759                 Adam Ounas       ALG   22                          Nice   
2205                 Adam Smith       ENG   28                   Bournemouth   
2277                Adam Szalai       HUN   31                      Mainz 05   
2473               Adam Webster       ENG   24                      Brighton   
2596             Adama Soumaoro       FRA   27                 Genoa / Lille   
2355               Adama Traore       ESP   23                        Wolves   
2356               Adama Traore       CIV   17                      Atalanta   
2605               Adama Traore       MLI   24                 Metz / Monaco   
1353            Ademola Lookman       ENG   21                    RB Leipzig   
100              Adil Aouchiche       FRA   17                     Paris S-G   
2286                 Adil Taoui       FRA   17                      Toulouse   
1526              Admir Mehmedi       SUI   28                     Wolfsburg   
1103              Adnan Januzaj       BEL   24                 Real Sociedad   
947              Adria Guerrero       ESP   21                      Valencia   
18                       Adrian       ESP   32                     Liverpool   
711              Adrian Embarba       ESP   27                      Espanyol   
1355               Adrian Lopez       ESP   31                       Osasuna   
1454            Adrian Mariappa       JAM   32                       Watford   
1457               Adrian Marin       ESP   22                        Alavés   
1940               Adrian Ramos       COL   33                       Granada   
1046               Adrien Hunou       FRA   25                        Rennes   
1298              Adrien Lebeau       FRA   20                    Strasbourg   
1921              Adrien Rabiot       FRA   24                      Juventus   
2168               Adrien